<a href="https://colab.research.google.com/github/panka-z/DataScience/blob/master/quora_question_sincerity_prediction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
# #Mounting google drive into colab
#from google.colab import drive
#drive.mount('/content/gdrive')

# accessing the shared link
# share the file or link from the drive
# go to your drive add the shared item to your drive

path="gdrive/My Drive/Project/"
file="train.csv"
with open(path+file,'r') as f:
  for line in f:
    print(line)
    break

qid,question_text,target



In [0]:
# all import statements

# python3 -m memory_profiler .\test.py to profile the memory usage of python
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
#from wordcloud import WordCloud as wc   # not needed
from nltk.corpus import stopwords
import matplotlib.pylab as pylab
import matplotlib.pyplot as plt
from pandas import get_dummies
import matplotlib as mpl
import seaborn as sns
import pandas as pd
import numpy as np
import matplotlib
import warnings
import sklearn
import string
import scipy
import numpy
import nltk
import json
import sys
import csv
import os
import time
import math

# more imports for NLP
from nltk.tokenize import word_tokenize
from nltk import pos_tag
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.preprocessing import LabelEncoder
from collections import defaultdict
from nltk.corpus import wordnet as wn
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn import model_selection, naive_bayes, svm
from sklearn.metrics import accuracy_score

#---- nltk libraries needed ----------------
import nltk
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger')

print('+'*100,'\n')
# printing versions of the important packages
# print('matplotlib: {}'.format(matplotlib.__version__))
# print('sklearn: {}'.format(sklearn.__version__))
# print('scipy: {}'.format(scipy.__version__))
# print('seaborn: {}'.format(sns.__version__))
# print('pandas: {}'.format(pd.__version__))
# print('numpy: {}'.format(np.__version__))
# print('Python: {}'.format(sys.version))

#debug to capture elapsed time
start_time = time.time()


def print_eda():
	# -------- not needed part as it does EDA  only -------------------------------------------

	# Number of words in the text
	train["num_words"] = train["question_text"].apply(lambda x: len(str(x).split()))
	test["num_words"] = test["question_text"].apply(lambda x: len(str(x).split()))
	print('maximum of num_words in train',train["num_words"].max())
	print('min of num_words in train',train["num_words"].min())
	print("maximum of  num_words in test",test["num_words"].max())
	print('min of num_words in train',test["num_words"].min())

	# Number of unique words in the text
	train["num_unique_words"] = train["question_text"].apply(lambda x: len(set(str(x).split())))
	test["num_unique_words"] = test["question_text"].apply(lambda x: len(set(str(x).split())))
	print('maximum of num_unique_words in train',train["num_unique_words"].max())
	print("maximum of num_unique_words in test",test["num_unique_words"].max())

	# Number of stopwords in the text
	#from nltk.corpus import stopwords
	eng_stopwords = set(stopwords.words("english"))
	train["num_stopwords"] = train["question_text"].apply(lambda x: len([w for w in str(x).lower().split() if w in eng_stopwords]))
	test["num_stopwords"] = test["question_text"].apply(lambda x: len([w for w in str(x).lower().split() if w in eng_stopwords]))
	print('maximum of num_stopwords in train',train["num_stopwords"].max())
	print("maximum of num_stopwords in test",test["num_stopwords"].max())

	# Number of punctuations in the text
	train["num_punctuations"] =train['question_text'].apply(lambda x: len([c for c in str(x) if c in string.punctuation]) )
	test["num_punctuations"] =test['question_text'].apply(lambda x: len([c for c in str(x) if c in string.punctuation]) )
	print('maximum of num_punctuations in train',train["num_punctuations"].max())
	print("maximum of num_punctuations in test",test["num_punctuations"].max())

	# lets figure out how many unique target values exist.
	# like we expect : 0 -> sincere qns and 1 -> un-sincere qns
	# You see number of unique item for Target with command below:
	train_target = train['target'].values
	np.unique(train_target)

	print("% of un-sincere qns is ", (train[train['target']==1].count())/train[train['target']==0].count())

	# visualising the imbalance in data set
	ax=sns.countplot(x='target',hue="target", data=train  ,linewidth=5,edgecolor=sns.color_palette("dark", 3))
	plt.title('Is data set imbalance?');

#-------------------------------------------------------------------------------------------------------------

def df_tokenize_and_lemmatize(df):

	# back up original question
	df['question']=df['question_text']
	# step 1: Change all the text to lower case. 
	# This is required as python interprets 'quora' and 'QUORA' differently
	df['question_text'] = [entry.lower() for entry in df['question_text']]

	# step 2 : Tokenization : In this each entry in the corpus will be broken 
	# into set of words	
	df['question_text']= [word_tokenize(entry) for entry in df['question_text']]
	print('tokenization done for df ..')
	
	# step 3, 4 and 5
	# Remove Stop words and Numeric data 
	# and perfom Word Stemming/Lemmenting.
	# WordNetLemmatizer requires Pos tags to understand if the word is noun or verb
	# or adjective etc. By default it is set to Noun
	tag_map = defaultdict(lambda : wn.NOUN)
	tag_map['J'] = wn.ADJ
	tag_map['V'] = wn.VERB
	tag_map['R'] = wn.ADV
	# the tag_map would map any tag to 'N' (Noun) except
	# Adjective to J, Verb -> v, Adverb -> R
	# that means if you get a Pronoun then it would still be mapped to Noun

	print('lemmatization starts for df ..')

	for index,entry in enumerate(df['question_text']):
		# Declaring Empty List to store the words that follow the rules for this step
		Final_words = []
		
		# Initializing WordNetLemmatizer()
		word_Lemmatized = WordNetLemmatizer()
		
		# pos_tag function below will provide the 'tag' 
		# i.e if the word is Noun(N) or Verb(V) or something else.
		for word, tag in pos_tag(entry):
			# Below condition is to check for Stop words and consider only 
			# alphabets
			if word not in stopwords.words('english') and word.isalpha():
				word_Final = word_Lemmatized.lemmatize(word,tag_map[tag[0]])
				Final_words.append(word_Final)
				
		# The final processed set of words for each iteration will be stored 
		# in 'question_text_final'
		df.loc[index,'question_text_final'] = str(Final_words)  
		
	print(df.head())
	return df

# ----------- main processing starts -----------------------

#loading the datasets
#path="C:/Suven/AdvML/Quora_question_prediction/"

train_large = pd.read_csv(path+'train.csv')
print('Training set loaded in => ',time.strftime("%H:%M:%S", time.gmtime(time.time() - start_time)))
test_large = pd.read_csv(path+'test.csv')
print('Testing set loaded in => ',time.strftime("%H:%M:%S", time.gmtime(time.time() - start_time)))

# create a local copy 
train=train_large
test=test_large

# print the details of the datasets
print('Train dataset ',train.info())
print('Shape of train:',train.shape)

# remove rows that have NA's
print('Train dataset Before Droping',train.shape)
train = train.dropna()
print('Train dataset After Droping',train.shape)

print('Test dataset ',test.info())
print('Shape of test:',test.shape)

# generate balanced datset
sample_count=min(int(train[train['target']==0].count()[0]),int(train [train['target']==1].count()[0]))
#down sample
#sample_count=math.floor(sample_count/10)
print('sample_count used=> ',sample_count)
train_sincere=train [train['target']==0].sample(n=sample_count) 
train_insincere=train [train['target']==1].sample(n=sample_count) 
train_balanced=pd.concat([train_sincere,train_insincere], axis=0,ignore_index=True)
train=train_balanced.sample(frac=1).reset_index(drop=True)
test=test.sample(n=sample_count).reset_index(drop=True)

# tokenize and lematize	
train=df_tokenize_and_lemmatize(train)
print('\n','Lematization of training set completed in =>',time.strftime("%H:%M:%S", time.gmtime(time.time() - start_time)))
test=df_tokenize_and_lemmatize(test)
print('\n','Lematization of testing set completed in =>',time.strftime("%H:%M:%S", time.gmtime(time.time() - start_time)))

Tfidf_vect = TfidfVectorizer()
Tfidf_vect.fit(train['question_text_final'])
Train_X_Tfidf = Tfidf_vect.transform(train['question_text_final'])

Test_X_Tfidf = Tfidf_vect.transform(test['question_text_final'])

# # to see the vocabulary that it has learned from the corpus
print(Tfidf_vect.vocabulary_)
print(Train_X_Tfidf)
print(Test_X_Tfidf)

# Output: 
# 1: Row number of ‘Train_X_Tfidf’, 
# 2: Unique Integer number of each word, 
# 3: Score calculated by TF-IDF Vectorizer


# fit the training dataset on the NB classifier
Naive = naive_bayes.MultinomialNB()
train_Y = train["target"]
Naive.fit(Train_X_Tfidf,train_Y)
# predict the labels on validation dataset
predictions_NB = Naive.predict(Test_X_Tfidf)
print(predictions_NB)


# Classifier - Algorithm - SVM
# fit the training dataset on the classifier
SVM = svm.SVC(C=1.0, kernel='linear', degree=3, gamma='auto')
SVM.fit(Train_X_Tfidf,train['target'])
# predict the labels on validation dataset
predictions_SVM = SVM.predict(Test_X_Tfidf)
print(predictions_SVM)

print('+'*100,'\n','Execution completed in =>',time.strftime("%H:%M:%S", time.gmtime(time.time() - start_time)))
#Execution completed in => 01:53:36

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++ 

Training set loaded in =>  00:00:02
Testing set loaded in =>  00:00:03
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1306122 entries, 0 to 1306121
Data columns (total 3 columns):
qid              1306122 non-null object
question_text    1306122 non-null object
target           1306122 non-null int64
dtypes: int64(1), object(2)
memory usage: 29.9+ MB
Train da

In [0]:
test['target_nb']=predictions_NB
test['target_svm']=predictions_SVM

In [0]:
print('-'*10,'Insincere questions as per Naive Bayes','-'*10)
print(test[test['target_nb']==1]['question'])
print('\n','+'*40,'\n')
print('-'*10,'Insincere questions as per SVM','-'*10)
print(test[test['target_svm']==1]['question'])

---------- Insincere questions as per Naive Bayes ----------
0        How should a president deal with something hap...
2        How can John Cate believe in man made delusion...
3                                   Was Jesus a Christian?
7        When will Hindus realise that running after ps...
10       How do you win back a good man you took for gr...
                               ...                        
80788    What's the difference between a minority gover...
80790    Do you know any compulsive liars, in person or...
80793                                 Who is Erin Crocker?
80802    Do some people in Hong Kong still prefer Briti...
80805    Can a community sustaining system have a regim...
Name: question, Length: 21575, dtype: object

 ++++++++++++++++++++++++++++++++++++++++ 

---------- Insincere questions as per SVM ----------
2        How can John Cate believe in man made delusion...
3                                   Was Jesus a Christian?
5                    Should I

In [0]:
#save the result to csv file
test.to_csv(path+'test_results', encoding='utf-8', index=False)

In [0]:
with open(path+'test_results','r') as f:
  for line in f:
    print(line)

qid,question_text,question,question_text_final,target_nb,target_svm

001a4d0e10c2d821aebe,"['how', 'should', 'a', 'president', 'deal', 'with', 'something', 'happening', 'in', 'his', 'or', 'her', 'state', 'without', 'infringing', 'on', 'the', 'authority', 'of', 'the', 'mayor', '?']",How should a president deal with something happening in his or her state without infringing on the authority of the mayor?,"['president', 'deal', 'something', 'happen', 'state', 'without', 'infringe', 'authority', 'mayor']",1,0

95126a44ce942793bc3f,"['what', 'are', 'the', 'perks', 'of', 'being', 'a', 'five', 'star', 'restaurant', 'chef', '?']",What are the perks of being a Five star restaurant chef?,"['perk', 'five', 'star', 'restaurant', 'chef']",0,0

8b2cf873582d6009866b,"['how', 'can', 'john', 'cate', 'believe', 'in', 'man', 'made', 'delusions', 'like', 'patriotism/nationalism', 'because', 'you', 'do', ""n't"", 'get', 'to', 'chose', 'where', 'you', 'were', 'born', '?']",How can John Cate believe in man m

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




aa28c8499b9499d49257,"['perception', 'question', '.', 'if', 'two', 'people', 'look', 'at', 'the', 'size', 'of', 'something', 'and', 'both', 'estimate', 'that', 'a', 'word', 'on', 'paper', 'is', 'about', 'an', 'inch', '.', 'would', 'that', 'likely', 'mean', 'it', 'was', 'close', 'in', 'size', 'to', 'both', 'and', 'that', 'the', 'other', 'person', 'wouldnt', 'really', 'see', 'it', '3x', 'as', 'large', 'as', 'you', '?']",Perception question. If two people look at the size of something and both estimate that a word on paper is about an inch. Would that likely mean it was close in size to both and that the other person wouldnt really see it 3x as large as you?,"['perception', 'question', 'two', 'people', 'look', 'size', 'something', 'estimate', 'word', 'paper', 'inch', 'would', 'likely', 'mean', 'close', 'size', 'person', 'wouldnt', 'really', 'see', 'large']",0,0

bcce90670f92812e3b06,"['what', 'are', 'some', 'ways', 'you', 'can', 'reduce', 'the', 'amount', 'of', 'calories', 'in', 'a', 'te

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



4e7aa38cd2678718108c,"['what', 'are', 'some', 'experiences', 'narcissists', 'have', 'had', 'with', 'therapy', '?']",What are some experiences narcissists have had with therapy?,"['experience', 'narcissist', 'therapy']",0,0

21dfdf736cbaac87e0bd,"['what', 'are', 'the', 'still', 'unanswered', 'questions', 'in', 'science', '?']",What are the still unanswered questions in science?,"['still', 'unanswered', 'question', 'science']",0,0

a85eac1a6eac92908143,"['aws', 'billed', 'me', '$', '38,576.29', 'due', 'to', 'probably', 'hacked', 'root', 'access', 'keys', '.', 'will', 'they', 'waive', 'the', 'charges', '?', 'what', 'can', 'i', 'show', 'them', 'to', 'support', 'my', 'case', '?']","AWS billed me $38,576.29 due to probably hacked root access keys. Will they waive the charges? What can I show them to support my case?","['aws', 'bill', 'due', 'probably', 'hacked', 'root', 'access', 'key', 'waive', 'charge', 'show', 'support', 'case']",0,0

62630e05b94b6100d272,"['are', 'the', 'patriots', 'assi